In [4]:
# text manipulation
import re
import string

# Data management
import pandas as pd
import numpy as np
from scipy.sparse import *
import scipy

# NLP
import nltk
import nltk.collocations as collocations
from nltk.tag import tnt
import spacy
import gensim
from gensim.models.phrases import Phrases, Phraser
from gensim.models import Word2Vec
from collections import defaultdict
import logging  # Setting up the loggings to monitor gensim
logging.basicConfig(format="%(levelname)s - %(asctime)s: %(message)s", datefmt= '%H:%M:%S', level=logging.INFO)

# sklearn
from sklearn.metrics import f1_score, confusion_matrix, accuracy_score, classification_report
from sklearn.model_selection import train_test_split, cross_val_score, cross_validate, GridSearchCV


# keras
from tensorflow import keras
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Flatten, LSTM, Conv1D, MaxPooling1D, Dropout, Activation, Embedding

#visualisation
import matplotlib.pyplot as plt
import seaborn as sns

import multiprocessing

%matplotlib inline

C:\ProgramData\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [ ]:
train = pd.read_csv('./train.csv')

In [ ]:
train.head()

In [ ]:
train.shape

In [ ]:
no_insincere = train[train['target']==1].target.count()
no_sincere = train[train['target']==0].target.count()

print('No. of insincere questions:', no_insincere)
print('No. of sincere questions:', no_sincere)
print('% of insincere questions:', train.target.mean())
print('Null score:', 1- train.target.mean())

In [ ]:
clean_questions = (re.sub("[^A-Za-z']+", ' ', q).lower() for q in train['question_text'])

In [ ]:
stopwords = list(nltk.corpus.stopwords.words('english'))

In [ ]:
%%time
# remove stop words and lower all characters
clean_questions = [' '.join(w for w in nltk.word_tokenize(q.lower()) if w not in stopwords) for q in clean_questions]

In [ ]:
train['clean_question'] = list(clean_questions)

In [ ]:
train.head()

In [ ]:
X = train['clean_question']
y = train.target

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, random_state=495, test_size=0.2)

In [ ]:
INPUT_LEN = 80

tokenizer = Tokenizer(num_words = MAX_NB_WORDS)
tokenizer.fit_on_texts(X_train)

Train_sequences = tokenizer.texts_to_sequences(X_train) 
X_train_data = pad_sequences(Train_sequences, maxlen=INPUT_LEN)

Test_sequences = tokenizer.texts_to_sequences(X_test)
X_test_data = pad_sequences(Test_sequences, maxlen=INPUT_LEN)

In [ ]:
word_index = tokenizer.word_index

In [ ]:
len(word_index)

### Word2Vec embedding using training data.

In [ ]:
w2v = Word2Vec(min_count=5,
               size = 100,
               window=4,
               workers=cores-1)

In [ ]:

w2v.build_vocab(X_train_tokens, progress_per=100000)

In [ ]:
words = list(w2v.wv.vocab)
len(words)

In [ ]:
%%time
w2v.train(token_list, total_examples=w2v.corpus_count, epochs=30, report_delay=1)

In [ ]:
w2v.wv.most_similar('nice') # Testing trained embedding

In [ ]:
# Tunning parameters
MAX_NB_WORDS = 100000
EMBEDDING_DIM = 300
LSTM_UNITS = 100
DROP = 0.2
RE_DROP = 0.2

In [ ]:
%%time
embedding_matrix = np.zeros((len(word_index), EMBEDDING_DIM))
for word, i in word_index.items():
    if word in w2v.vocab:
        embedding_matrix[i] = word2vec.word_vec(word)
print('Null word embeddings: %d' % np.sum(np.sum(embedding_matrix, axis=1) == 0))


#### LSTM

In [ ]:
## Network architecture
model = Sequential()

model.add(Embedding(MAX_NB_WORDS, EMBEDDING_DIM, weights = [embedding_matrix], input_length=INPUT_LEN)) 
model.add(LSTM(LSTM_UNITS, dropout=DROP, recurrent_dropout=RE_DROP))
model.add(Dense(1, activation='sigmoid')) 
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

model.fit(X_train_data, y_train, validation_split=0.4, epochs=3)

In [ ]:
%%time
y_pred = model_conv.predict(X_test_data, workers=6)

In [ ]:
y_predRound = [ 1 if y >= 0.2 else 0  for y in y_pred]

In [ ]:
print('accuracy %s' % accuracy_score(y_test, y_predRound))
print(classification_report(y_test, y_predRound))
confusion_matrix(y_test, y_predRound)

#### Conv1D LSTM

In [17]:
# Tunning parameters
MAX_NB_WORDS = 100000
EMBEDDING_DIM = 200
LSTM_UNITS = 200
DROP = 0.2
RE_DROP = 0.2
FILTERS = 128
KERNEL = 1
POOL_SIZE = 4

In [ ]:
%%time
def create_conv_model():
    model_conv = Sequential()
    model_conv.add(Embedding(MAX_NB_WORDS, EMBEDDING_DIM, input_length=INPUT_LEN))
    model_conv.add(Dropout(DROP))
    model_conv.add(Conv1D(FILTERS, KERNEL, activation='relu'))
    model_conv.add(MaxPooling1D(pool_size=POOL_SIZE)) # Return max value from 4 adjacent values, reduce computational requirement and reduce overfitting.
    model_conv.add(LSTM(LSTM_UNITS))
    model_conv.add(Dense(1, activation='sigmoid'))
    model_conv.compile(loss='binary_crossentropy', optimizer='adam',    metrics=['accuracy'])
    return model_conv
model_conv = create_conv_model()
model_conv.fit(X_train_data, y_train, validation_split=0.4, epochs = 3)

# Reduced computation time to 1/4.

In [ ]:
%%time
y_pred = model_conv.predict(X_test_data, workers=6)

In [ ]:
y_predRound = [ 1 if y >= 0.2 else 0  for y in y_pred]

In [ ]:
print('accuracy %s' % accuracy_score(y_test, y_predRound))
print(classification_report(y_test, y_predRound))
confusion_matrix(y_test, y_predRound)

### Using google pre-trained Word2Vec model

In [21]:
%%time

# model pre-trained by Google
wv_google = gensim.models.KeyedVectors.load_word2vec_format("GoogleNews-vectors-negative300.bin.gz", binary=True)
wv_google.init_sims(replace=True)

INFO - 23:26:16: loading projection weights from GoogleNews-vectors-negative300.bin.gz
INFO - 23:28:20: loaded (3000000, 300) matrix from GoogleNews-vectors-negative300.bin.gz
INFO - 23:28:20: precomputing L2-norms of word weight vectors


Wall time: 2min 35s


In [22]:
wv_google.wv.most_similar('nice')

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `wv` (Attribute will be removed in 4.0.0, use self instead).
  """Entry point for launching an IPython kernel.


[('good', 0.6836092472076416),
 ('lovely', 0.6676311492919922),
 ('neat', 0.6616737246513367),
 ('fantastic', 0.6569241285324097),
 ('wonderful', 0.6561347246170044),
 ('terrific', 0.6552367210388184),
 ('great', 0.6454657316207886),
 ('awesome', 0.6404187083244324),
 ('nicer', 0.6302444934844971),
 ('decent', 0.5993332266807556)]

In [2]:
# Tunning parameters
MAX_NB_WORDS = 100000
EMBEDDING_DIM = 300
LSTM_UNITS = 100
DROP = 0.2
RE_DROP = 0.2

In [3]:
%%time
embedding_matrix = np.zeros((len(word_index), EMBEDDING_DIM))
for word, i in word_index.items():
    if word in wv_google.vocab:
        embedding_matrix[i] = wv_google.word_vec(word)
print('Null word embeddings: %d' % np.sum(np.sum(embedding_matrix, axis=1) == 0))

NameError: name 'np' is not defined


#### LSTM

In [25]:
%%time
#### LSTM## Network architecture
model = Sequential()

model.add(Embedding(MAX_NB_WORDS, EMBEDDING_DIM, weights = [embedding_matrix], input_length=INPUT_LEN)) 
model.add(LSTM(LSTM_UNITS, dropout=DROP, recurrent_dropout=RE_DROP))
model.add(Dense(1, activation='sigmoid')) 
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

model.fit(X_train_data, y_train, validation_split=0.4, epochs=3)

C:\ProgramData\Anaconda3\lib\site-packages\tensorflow\python\ops\gradients_impl.py:112: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "
C:\ProgramData\Anaconda3\lib\site-packages\tensorflow\python\ops\gradients_impl.py:112: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Train on 626938 samples, validate on 417959 samples
Epoch 1/3


  6176/626938 [..............................] - ETA: 24:51:51 - loss: 0.6896 - acc: 0.718 - ETA: 13:07:31 - loss: 0.6837 - acc: 0.750 - ETA: 9:12:24 - loss: 0.6760 - acc: 0.802 - ETA: 7:15:54 - loss: 0.6670 - acc: 0.82 - ETA: 6:05:25 - loss: 0.6540 - acc: 0.85 - ETA: 5:21:22 - loss: 0.6452 - acc: 0.85 - ETA: 4:46:57 - loss: 0.6312 - acc: 0.87 - ETA: 4:20:47 - loss: 0.6158 - acc: 0.88 - ETA: 4:00:28 - loss: 0.6053 - acc: 0.88 - ETA: 3:44:18 - loss: 0.5853 - acc: 0.89 - ETA: 3:30:59 - loss: 0.5631 - acc: 0.89 - ETA: 3:20:25 - loss: 0.5387 - acc: 0.90 - ETA: 3:10:59 - loss: 0.5109 - acc: 0.90 - ETA: 3:02:43 - loss: 0.5168 - acc: 0.90 - ETA: 2:55:50 - loss: 0.4907 - acc: 0.90 - ETA: 2:49:50 - loss: 0.4682 - acc: 0.91 - ETA: 2:44:16 - loss: 0.4563 - acc: 0.91 - ETA: 2:39:31 - loss: 0.4391 - acc: 0.91 - ETA: 2:35:12 - loss: 0.4172 - acc: 0.91 - ETA: 2:31:19 - loss: 0.4035 - acc: 0.92 - ETA: 2:27:41 - loss: 0.3854 - acc: 0.92 - ETA: 2:24:25 - loss: 0.3689 - acc: 0.92 - ETA: 2:21:29 - loss: 0

 18592/626938 [..............................] - ETA: 1:21:38 - loss: 0.1846 - acc: 0.94 - ETA: 1:21:37 - loss: 0.1846 - acc: 0.94 - ETA: 1:21:36 - loss: 0.1845 - acc: 0.94 - ETA: 1:21:35 - loss: 0.1846 - acc: 0.94 - ETA: 1:21:34 - loss: 0.1844 - acc: 0.94 - ETA: 1:21:34 - loss: 0.1844 - acc: 0.94 - ETA: 1:21:33 - loss: 0.1840 - acc: 0.94 - ETA: 1:21:32 - loss: 0.1841 - acc: 0.94 - ETA: 1:21:31 - loss: 0.1839 - acc: 0.94 - ETA: 1:21:30 - loss: 0.1837 - acc: 0.94 - ETA: 1:21:29 - loss: 0.1836 - acc: 0.94 - ETA: 1:21:29 - loss: 0.1832 - acc: 0.94 - ETA: 1:21:28 - loss: 0.1834 - acc: 0.94 - ETA: 1:21:30 - loss: 0.1837 - acc: 0.94 - ETA: 1:21:33 - loss: 0.1835 - acc: 0.94 - ETA: 1:21:33 - loss: 0.1833 - acc: 0.94 - ETA: 1:21:31 - loss: 0.1835 - acc: 0.94 - ETA: 1:21:30 - loss: 0.1835 - acc: 0.94 - ETA: 1:21:32 - loss: 0.1835 - acc: 0.94 - ETA: 1:21:32 - loss: 0.1835 - acc: 0.94 - ETA: 1:21:31 - loss: 0.1832 - acc: 0.94 - ETA: 1:21:31 - loss: 0.1830 - acc: 0.94 - ETA: 1:21:32 - loss: 0.1828

 24800/626938 [>.............................] - ETA: 1:20:47 - loss: 0.1732 - acc: 0.94 - ETA: 1:20:46 - loss: 0.1731 - acc: 0.94 - ETA: 1:20:46 - loss: 0.1730 - acc: 0.94 - ETA: 1:20:45 - loss: 0.1729 - acc: 0.94 - ETA: 1:20:45 - loss: 0.1726 - acc: 0.94 - ETA: 1:20:44 - loss: 0.1728 - acc: 0.94 - ETA: 1:20:43 - loss: 0.1728 - acc: 0.94 - ETA: 1:20:43 - loss: 0.1727 - acc: 0.94 - ETA: 1:20:42 - loss: 0.1728 - acc: 0.94 - ETA: 1:20:42 - loss: 0.1727 - acc: 0.94 - ETA: 1:20:42 - loss: 0.1732 - acc: 0.94 - ETA: 1:20:41 - loss: 0.1731 - acc: 0.94 - ETA: 1:20:40 - loss: 0.1732 - acc: 0.94 - ETA: 1:20:40 - loss: 0.1732 - acc: 0.94 - ETA: 1:20:40 - loss: 0.1731 - acc: 0.94 - ETA: 1:20:39 - loss: 0.1734 - acc: 0.94 - ETA: 1:20:39 - loss: 0.1733 - acc: 0.94 - ETA: 1:20:38 - loss: 0.1735 - acc: 0.94 - ETA: 1:20:38 - loss: 0.1733 - acc: 0.94 - ETA: 1:20:37 - loss: 0.1732 - acc: 0.94 - ETA: 1:20:37 - loss: 0.1730 - acc: 0.94 - ETA: 1:20:37 - loss: 0.1730 - acc: 0.94 - ETA: 1:20:38 - loss: 0.1730

...

604608/626938 [===========================>..] - ETA: 2:59 - loss: 0.0831 - acc: 0.968 - ETA: 2:59 - loss: 0.0831 - acc: 0.968 - ETA: 2:59 - loss: 0.0831 - acc: 0.968 - ETA: 2:59 - loss: 0.0831 - acc: 0.968 - ETA: 2:59 - loss: 0.0831 - acc: 0.968 - ETA: 2:58 - loss: 0.0831 - acc: 0.968 - ETA: 2:58 - loss: 0.0831 - acc: 0.968 - ETA: 2:58 - loss: 0.0831 - acc: 0.968 - ETA: 2:58 - loss: 0.0831 - acc: 0.968 - ETA: 2:58 - loss: 0.0831 - acc: 0.968 - ETA: 2:57 - loss: 0.0831 - acc: 0.968 - ETA: 2:57 - loss: 0.0831 - acc: 0.968 - ETA: 2:57 - loss: 0.0831 - acc: 0.968 - ETA: 2:57 - loss: 0.0831 - acc: 0.968 - ETA: 2:57 - loss: 0.0831 - acc: 0.968 - ETA: 2:56 - loss: 0.0831 - acc: 0.968 - ETA: 2:56 - loss: 0.0831 - acc: 0.968 - ETA: 2:56 - loss: 0.0831 - acc: 0.968 - ETA: 2:56 - loss: 0.0831 - acc: 0.968 - ETA: 2:56 - loss: 0.0831 - acc: 0.968 - ETA: 2:55 - loss: 0.0831 - acc: 0.968 - ETA: 2:55 - loss: 0.0831 - acc: 0.968 - ETA: 2:55 - loss: 0.0831 - acc: 0.968 - ETA: 2:55 - loss: 0.0831 - acc:

611136/626938 [============================>.] - ETA: 2:19 - loss: 0.0831 - acc: 0.968 - ETA: 2:19 - loss: 0.0831 - acc: 0.968 - ETA: 2:18 - loss: 0.0831 - acc: 0.968 - ETA: 2:18 - loss: 0.0831 - acc: 0.968 - ETA: 2:18 - loss: 0.0831 - acc: 0.968 - ETA: 2:18 - loss: 0.0831 - acc: 0.968 - ETA: 2:18 - loss: 0.0831 - acc: 0.968 - ETA: 2:17 - loss: 0.0831 - acc: 0.968 - ETA: 2:17 - loss: 0.0831 - acc: 0.968 - ETA: 2:17 - loss: 0.0831 - acc: 0.968 - ETA: 2:17 - loss: 0.0831 - acc: 0.968 - ETA: 2:17 - loss: 0.0831 - acc: 0.968 - ETA: 2:16 - loss: 0.0831 - acc: 0.968 - ETA: 2:16 - loss: 0.0831 - acc: 0.968 - ETA: 2:16 - loss: 0.0831 - acc: 0.968 - ETA: 2:16 - loss: 0.0831 - acc: 0.968 - ETA: 2:16 - loss: 0.0831 - acc: 0.968 - ETA: 2:15 - loss: 0.0831 - acc: 0.968 - ETA: 2:15 - loss: 0.0831 - acc: 0.968 - ETA: 2:15 - loss: 0.0831 - acc: 0.968 - ETA: 2:15 - loss: 0.0831 - acc: 0.968 - ETA: 2:15 - loss: 0.0831 - acc: 0.968 - ETA: 2:14 - loss: 0.0831 - acc: 0.968 - ETA: 2:14 - loss: 0.0831 - acc:

617696/626938 [============================>.] - ETA: 1:38 - loss: 0.0831 - acc: 0.968 - ETA: 1:38 - loss: 0.0831 - acc: 0.968 - ETA: 1:38 - loss: 0.0831 - acc: 0.968 - ETA: 1:37 - loss: 0.0831 - acc: 0.968 - ETA: 1:37 - loss: 0.0831 - acc: 0.968 - ETA: 1:37 - loss: 0.0831 - acc: 0.968 - ETA: 1:37 - loss: 0.0831 - acc: 0.968 - ETA: 1:37 - loss: 0.0831 - acc: 0.968 - ETA: 1:36 - loss: 0.0831 - acc: 0.968 - ETA: 1:36 - loss: 0.0831 - acc: 0.968 - ETA: 1:36 - loss: 0.0831 - acc: 0.968 - ETA: 1:36 - loss: 0.0831 - acc: 0.968 - ETA: 1:36 - loss: 0.0831 - acc: 0.968 - ETA: 1:35 - loss: 0.0831 - acc: 0.968 - ETA: 1:35 - loss: 0.0831 - acc: 0.968 - ETA: 1:35 - loss: 0.0831 - acc: 0.968 - ETA: 1:35 - loss: 0.0831 - acc: 0.968 - ETA: 1:35 - loss: 0.0831 - acc: 0.968 - ETA: 1:34 - loss: 0.0831 - acc: 0.968 - ETA: 1:34 - loss: 0.0831 - acc: 0.968 - ETA: 1:34 - loss: 0.0831 - acc: 0.968 - ETA: 1:34 - loss: 0.0831 - acc: 0.968 - ETA: 1:34 - loss: 0.0831 - acc: 0.968 - ETA: 1:33 - loss: 0.0831 - acc:

624576/626938 [============================>.] - ETA: 57s - loss: 0.0832 - acc: 0.96 - ETA: 57s - loss: 0.0832 - acc: 0.96 - ETA: 57s - loss: 0.0832 - acc: 0.96 - ETA: 56s - loss: 0.0832 - acc: 0.96 - ETA: 56s - loss: 0.0832 - acc: 0.96 - ETA: 56s - loss: 0.0832 - acc: 0.96 - ETA: 56s - loss: 0.0832 - acc: 0.96 - ETA: 56s - loss: 0.0832 - acc: 0.96 - ETA: 55s - loss: 0.0832 - acc: 0.96 - ETA: 55s - loss: 0.0832 - acc: 0.96 - ETA: 55s - loss: 0.0832 - acc: 0.96 - ETA: 55s - loss: 0.0832 - acc: 0.96 - ETA: 55s - loss: 0.0832 - acc: 0.96 - ETA: 54s - loss: 0.0832 - acc: 0.96 - ETA: 54s - loss: 0.0832 - acc: 0.96 - ETA: 54s - loss: 0.0832 - acc: 0.96 - ETA: 54s - loss: 0.0832 - acc: 0.96 - ETA: 54s - loss: 0.0832 - acc: 0.96 - ETA: 53s - loss: 0.0832 - acc: 0.96 - ETA: 53s - loss: 0.0832 - acc: 0.96 - ETA: 53s - loss: 0.0832 - acc: 0.96 - ETA: 53s - loss: 0.0832 - acc: 0.96 - ETA: 53s - loss: 0.0832 - acc: 0.96 - ETA: 52s - loss: 0.0832 - acc: 0.96 - ETA: 52s - loss: 0.0832 - acc: 0.96 - E

626938/626938 [==============================] - ETA: 14s - loss: 0.0832 - acc: 0.96 - ETA: 14s - loss: 0.0833 - acc: 0.96 - ETA: 14s - loss: 0.0833 - acc: 0.96 - ETA: 13s - loss: 0.0833 - acc: 0.96 - ETA: 13s - loss: 0.0833 - acc: 0.96 - ETA: 13s - loss: 0.0833 - acc: 0.96 - ETA: 13s - loss: 0.0833 - acc: 0.96 - ETA: 13s - loss: 0.0833 - acc: 0.96 - ETA: 12s - loss: 0.0832 - acc: 0.96 - ETA: 12s - loss: 0.0832 - acc: 0.96 - ETA: 12s - loss: 0.0832 - acc: 0.96 - ETA: 12s - loss: 0.0832 - acc: 0.96 - ETA: 12s - loss: 0.0832 - acc: 0.96 - ETA: 11s - loss: 0.0832 - acc: 0.96 - ETA: 11s - loss: 0.0832 - acc: 0.96 - ETA: 11s - loss: 0.0832 - acc: 0.96 - ETA: 11s - loss: 0.0832 - acc: 0.96 - ETA: 11s - loss: 0.0832 - acc: 0.96 - ETA: 10s - loss: 0.0832 - acc: 0.96 - ETA: 10s - loss: 0.0832 - acc: 0.96 - ETA: 10s - loss: 0.0832 - acc: 0.96 - ETA: 10s - loss: 0.0832 - acc: 0.96 - ETA: 10s - loss: 0.0832 - acc: 0.96 - ETA: 9s - loss: 0.0832 - acc: 0.9682 - ETA: 9s - loss: 0.0832 - acc: 0.968 - 

In [28]:
%%time
y_pred = model.predict(X_test_data, workers=6)

Wall time: 8min 26s


In [1]:
y_predRound = [ 1 if y >= 0.2 else 0  for y in y_pred]

NameError: name 'y_pred' is not defined

In [50]:
print('accuracy %s' % accuracy_score(y_test, y_predRound))
print(classification_report(y_test, y_predRound))
confusion_matrix(y_test, y_predRound)

accuracy 0.9385395731648961
              precision    recall  f1-score   support

           0       0.98      0.95      0.97    245063
           1       0.50      0.73      0.60     16162

   micro avg       0.94      0.94      0.94    261225
   macro avg       0.74      0.84      0.78    261225
weighted avg       0.95      0.94      0.94    261225



array([[233311,  11752],
       [  4303,  11859]], dtype=int64)

#### Conv1D LSTM

In [41]:
# Tunning parameters
MAX_NB_WORDS = 100000
EMBEDDING_DIM = 200
LSTM_UNITS = 200
DROP = 0.2
RE_DROP = 0.2
FILTERS = 128
KERNEL = 1
POOL_SIZE = 4

In [46]:
%%time
def create_conv_model():
    model_conv = Sequential()
    model_conv.add(Embedding(MAX_NB_WORDS, EMBEDDING_DIM, input_length=INPUT_LEN))
    model_conv.add(Dropout(DROP))
    model_conv.add(Conv1D(FILTERS, KERNEL, activation='relu'))
    model_conv.add(MaxPooling1D(pool_size=POOL_SIZE)) # Return max value from 4 adjacent values, reduce computational requirement and reduce overfitting.
    model_conv.add(LSTM(LSTM_UNITS))
    model_conv.add(Dense(1, activation='sigmoid'))
    model_conv.compile(loss='binary_crossentropy', optimizer='adam',    metrics=['accuracy'])
    return model_conv

model_conv = create_conv_model()
model_conv.fit(X_train_data, y_train, validation_split=0.4, epochs = 3)

# Reduced computation time to 1/4.

C:\ProgramData\Anaconda3\lib\site-packages\tensorflow\python\ops\gradients_impl.py:112: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "
C:\ProgramData\Anaconda3\lib\site-packages\tensorflow\python\ops\gradients_impl.py:112: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Train on 626938 samples, validate on 417959 samples
Epoch 1/3


  6464/626938 [..............................] - ETA: 8:33:36 - loss: 0.6992 - acc: 0.06 - ETA: 4:27:23 - loss: 0.6805 - acc: 0.46 - ETA: 3:04:34 - loss: 0.6586 - acc: 0.61 - ETA: 2:23:14 - loss: 0.6315 - acc: 0.69 - ETA: 1:58:22 - loss: 0.5935 - acc: 0.75 - ETA: 1:41:44 - loss: 0.5692 - acc: 0.77 - ETA: 1:29:51 - loss: 0.5365 - acc: 0.79 - ETA: 1:20:59 - loss: 0.4986 - acc: 0.81 - ETA: 1:14:16 - loss: 0.4886 - acc: 0.82 - ETA: 1:08:47 - loss: 0.4948 - acc: 0.82 - ETA: 1:04:13 - loss: 0.4624 - acc: 0.84 - ETA: 1:00:27 - loss: 0.4355 - acc: 0.85 - ETA: 57:15 - loss: 0.4132 - acc: 0.8606 - ETA: 54:29 - loss: 0.3884 - acc: 0.87 - ETA: 52:04 - loss: 0.3670 - acc: 0.87 - ETA: 49:59 - loss: 0.3532 - acc: 0.88 - ETA: 48:11 - loss: 0.3513 - acc: 0.88 - ETA: 46:37 - loss: 0.3393 - acc: 0.89 - ETA: 45:08 - loss: 0.3391 - acc: 0.89 - ETA: 43:49 - loss: 0.3243 - acc: 0.89 - ETA: 42:40 - loss: 0.3202 - acc: 0.89 - ETA: 41:38 - loss: 0.3250 - acc: 0.89 - ETA: 40:39 - loss: 0.3129 - acc: 0.90 - ETA: 

 26048/626938 [>.............................] - ETA: 19:22 - loss: 0.1919 - acc: 0.93 - ETA: 19:22 - loss: 0.1916 - acc: 0.93 - ETA: 19:22 - loss: 0.1915 - acc: 0.93 - ETA: 19:22 - loss: 0.1913 - acc: 0.93 - ETA: 19:22 - loss: 0.1911 - acc: 0.93 - ETA: 19:22 - loss: 0.1911 - acc: 0.93 - ETA: 19:22 - loss: 0.1909 - acc: 0.93 - ETA: 19:21 - loss: 0.1906 - acc: 0.93 - ETA: 19:21 - loss: 0.1908 - acc: 0.93 - ETA: 19:21 - loss: 0.1907 - acc: 0.93 - ETA: 19:21 - loss: 0.1907 - acc: 0.93 - ETA: 19:21 - loss: 0.1909 - acc: 0.93 - ETA: 19:21 - loss: 0.1911 - acc: 0.93 - ETA: 19:20 - loss: 0.1909 - acc: 0.93 - ETA: 19:20 - loss: 0.1911 - acc: 0.93 - ETA: 19:20 - loss: 0.1909 - acc: 0.93 - ETA: 19:20 - loss: 0.1910 - acc: 0.93 - ETA: 19:20 - loss: 0.1908 - acc: 0.93 - ETA: 19:20 - loss: 0.1905 - acc: 0.93 - ETA: 19:20 - loss: 0.1906 - acc: 0.93 - ETA: 19:19 - loss: 0.1904 - acc: 0.93 - ETA: 19:19 - loss: 0.1906 - acc: 0.93 - ETA: 19:19 - loss: 0.1907 - acc: 0.93 - ETA: 19:19 - loss: 0.1905 - acc

 32576/626938 [>.............................] - ETA: 18:55 - loss: 0.1816 - acc: 0.93 - ETA: 18:55 - loss: 0.1815 - acc: 0.93 - ETA: 18:55 - loss: 0.1816 - acc: 0.93 - ETA: 18:54 - loss: 0.1816 - acc: 0.93 - ETA: 18:54 - loss: 0.1814 - acc: 0.93 - ETA: 18:54 - loss: 0.1813 - acc: 0.93 - ETA: 18:54 - loss: 0.1812 - acc: 0.94 - ETA: 18:54 - loss: 0.1810 - acc: 0.94 - ETA: 18:54 - loss: 0.1810 - acc: 0.94 - ETA: 18:54 - loss: 0.1808 - acc: 0.94 - ETA: 18:54 - loss: 0.1808 - acc: 0.94 - ETA: 18:54 - loss: 0.1807 - acc: 0.94 - ETA: 18:54 - loss: 0.1806 - acc: 0.94 - ETA: 18:53 - loss: 0.1804 - acc: 0.94 - ETA: 18:53 - loss: 0.1806 - acc: 0.94 - ETA: 18:53 - loss: 0.1804 - acc: 0.94 - ETA: 18:53 - loss: 0.1803 - acc: 0.94 - ETA: 18:53 - loss: 0.1802 - acc: 0.94 - ETA: 18:53 - loss: 0.1803 - acc: 0.94 - ETA: 18:53 - loss: 0.1804 - acc: 0.94 - ETA: 18:52 - loss: 0.1803 - acc: 0.94 - ETA: 18:52 - loss: 0.1802 - acc: 0.94 - ETA: 18:52 - loss: 0.1801 - acc: 0.94 - ETA: 18:52 - loss: 0.1799 - acc

...

600896/626938 [===========================>..] - ETA: 1:00 - loss: 0.1009 - acc: 0.960 - ETA: 1:00 - loss: 0.1009 - acc: 0.960 - ETA: 1:00 - loss: 0.1009 - acc: 0.960 - ETA: 1:00 - loss: 0.1009 - acc: 0.960 - ETA: 1:00 - loss: 0.1009 - acc: 0.960 - ETA: 1:00 - loss: 0.1009 - acc: 0.960 - ETA: 1:00 - loss: 0.1009 - acc: 0.960 - ETA: 1:00 - loss: 0.1009 - acc: 0.960 - ETA: 59s - loss: 0.1009 - acc: 0.960 - ETA: 59s - loss: 0.1009 - acc: 0.96 - ETA: 59s - loss: 0.1009 - acc: 0.96 - ETA: 59s - loss: 0.1009 - acc: 0.96 - ETA: 59s - loss: 0.1009 - acc: 0.96 - ETA: 59s - loss: 0.1009 - acc: 0.96 - ETA: 59s - loss: 0.1009 - acc: 0.96 - ETA: 59s - loss: 0.1009 - acc: 0.96 - ETA: 59s - loss: 0.1009 - acc: 0.96 - ETA: 59s - loss: 0.1009 - acc: 0.96 - ETA: 59s - loss: 0.1009 - acc: 0.96 - ETA: 59s - loss: 0.1009 - acc: 0.96 - ETA: 59s - loss: 0.1009 - acc: 0.96 - ETA: 59s - loss: 0.1009 - acc: 0.96 - ETA: 59s - loss: 0.1009 - acc: 0.96 - ETA: 59s - loss: 0.1009 - acc: 0.96 - ETA: 59s - loss: 0.100

607776/626938 [============================>.] - ETA: 47s - loss: 0.1010 - acc: 0.96 - ETA: 47s - loss: 0.1010 - acc: 0.96 - ETA: 47s - loss: 0.1010 - acc: 0.96 - ETA: 47s - loss: 0.1010 - acc: 0.96 - ETA: 47s - loss: 0.1010 - acc: 0.96 - ETA: 47s - loss: 0.1010 - acc: 0.96 - ETA: 47s - loss: 0.1010 - acc: 0.96 - ETA: 47s - loss: 0.1010 - acc: 0.96 - ETA: 47s - loss: 0.1010 - acc: 0.96 - ETA: 47s - loss: 0.1010 - acc: 0.96 - ETA: 47s - loss: 0.1010 - acc: 0.96 - ETA: 47s - loss: 0.1010 - acc: 0.96 - ETA: 47s - loss: 0.1010 - acc: 0.96 - ETA: 47s - loss: 0.1010 - acc: 0.96 - ETA: 47s - loss: 0.1010 - acc: 0.96 - ETA: 46s - loss: 0.1010 - acc: 0.96 - ETA: 46s - loss: 0.1010 - acc: 0.96 - ETA: 46s - loss: 0.1010 - acc: 0.96 - ETA: 46s - loss: 0.1010 - acc: 0.96 - ETA: 46s - loss: 0.1010 - acc: 0.96 - ETA: 46s - loss: 0.1010 - acc: 0.96 - ETA: 46s - loss: 0.1010 - acc: 0.96 - ETA: 46s - loss: 0.1010 - acc: 0.96 - ETA: 46s - loss: 0.1010 - acc: 0.96 - ETA: 46s - loss: 0.1010 - acc: 0.96 - E

614656/626938 [============================>.] - ETA: 35s - loss: 0.1011 - acc: 0.96 - ETA: 35s - loss: 0.1011 - acc: 0.96 - ETA: 35s - loss: 0.1011 - acc: 0.96 - ETA: 35s - loss: 0.1011 - acc: 0.96 - ETA: 34s - loss: 0.1011 - acc: 0.96 - ETA: 34s - loss: 0.1011 - acc: 0.96 - ETA: 34s - loss: 0.1011 - acc: 0.96 - ETA: 34s - loss: 0.1011 - acc: 0.96 - ETA: 34s - loss: 0.1011 - acc: 0.96 - ETA: 34s - loss: 0.1011 - acc: 0.96 - ETA: 34s - loss: 0.1011 - acc: 0.96 - ETA: 34s - loss: 0.1011 - acc: 0.96 - ETA: 34s - loss: 0.1011 - acc: 0.96 - ETA: 34s - loss: 0.1011 - acc: 0.96 - ETA: 34s - loss: 0.1011 - acc: 0.96 - ETA: 34s - loss: 0.1011 - acc: 0.96 - ETA: 34s - loss: 0.1011 - acc: 0.96 - ETA: 34s - loss: 0.1011 - acc: 0.96 - ETA: 34s - loss: 0.1011 - acc: 0.96 - ETA: 34s - loss: 0.1011 - acc: 0.96 - ETA: 34s - loss: 0.1011 - acc: 0.96 - ETA: 33s - loss: 0.1011 - acc: 0.96 - ETA: 33s - loss: 0.1011 - acc: 0.96 - ETA: 33s - loss: 0.1011 - acc: 0.96 - ETA: 33s - loss: 0.1011 - acc: 0.96 - E

621536/626938 [============================>.] - ETA: 22s - loss: 0.1012 - acc: 0.96 - ETA: 22s - loss: 0.1012 - acc: 0.96 - ETA: 22s - loss: 0.1012 - acc: 0.96 - ETA: 22s - loss: 0.1012 - acc: 0.96 - ETA: 22s - loss: 0.1012 - acc: 0.96 - ETA: 22s - loss: 0.1012 - acc: 0.96 - ETA: 22s - loss: 0.1012 - acc: 0.96 - ETA: 22s - loss: 0.1012 - acc: 0.96 - ETA: 22s - loss: 0.1012 - acc: 0.96 - ETA: 22s - loss: 0.1012 - acc: 0.96 - ETA: 21s - loss: 0.1012 - acc: 0.96 - ETA: 21s - loss: 0.1012 - acc: 0.96 - ETA: 21s - loss: 0.1012 - acc: 0.96 - ETA: 21s - loss: 0.1012 - acc: 0.96 - ETA: 21s - loss: 0.1012 - acc: 0.96 - ETA: 21s - loss: 0.1012 - acc: 0.96 - ETA: 21s - loss: 0.1012 - acc: 0.96 - ETA: 21s - loss: 0.1012 - acc: 0.96 - ETA: 21s - loss: 0.1012 - acc: 0.96 - ETA: 21s - loss: 0.1012 - acc: 0.96 - ETA: 21s - loss: 0.1012 - acc: 0.96 - ETA: 21s - loss: 0.1012 - acc: 0.96 - ETA: 21s - loss: 0.1012 - acc: 0.96 - ETA: 21s - loss: 0.1012 - acc: 0.96 - ETA: 21s - loss: 0.1012 - acc: 0.96 - E

626938/626938 [==============================] - ETA: 9s - loss: 0.1012 - acc: 0.960 - ETA: 9s - loss: 0.1012 - acc: 0.960 - ETA: 9s - loss: 0.1012 - acc: 0.960 - ETA: 9s - loss: 0.1012 - acc: 0.960 - ETA: 9s - loss: 0.1012 - acc: 0.960 - ETA: 9s - loss: 0.1012 - acc: 0.960 - ETA: 9s - loss: 0.1012 - acc: 0.960 - ETA: 9s - loss: 0.1012 - acc: 0.960 - ETA: 9s - loss: 0.1012 - acc: 0.960 - ETA: 9s - loss: 0.1012 - acc: 0.960 - ETA: 9s - loss: 0.1012 - acc: 0.960 - ETA: 9s - loss: 0.1012 - acc: 0.960 - ETA: 9s - loss: 0.1012 - acc: 0.960 - ETA: 9s - loss: 0.1012 - acc: 0.960 - ETA: 9s - loss: 0.1012 - acc: 0.960 - ETA: 8s - loss: 0.1012 - acc: 0.960 - ETA: 8s - loss: 0.1012 - acc: 0.960 - ETA: 8s - loss: 0.1012 - acc: 0.960 - ETA: 8s - loss: 0.1012 - acc: 0.960 - ETA: 8s - loss: 0.1012 - acc: 0.960 - ETA: 8s - loss: 0.1012 - acc: 0.960 - ETA: 8s - loss: 0.1012 - acc: 0.960 - ETA: 8s - loss: 0.1012 - acc: 0.960 - ETA: 8s - loss: 0.1012 - acc: 0.960 - ETA: 8s - loss: 0.1012 - acc: 0.960 - E

In [47]:
%%time
y_pred = model_conv.predict(X_test_data, workers=6)

Wall time: 2min 15s


In [60]:
y_predRound = [ 1 if y >= 0.2 else 0  for y in y_pred]

In [61]:
print('accuracy %s' % accuracy_score(y_test, y_predRound))
print(classification_report(y_test, y_predRound))
confusion_matrix(y_test, y_predRound)

accuracy 0.9267910804861709
              precision    recall  f1-score   support

           0       0.99      0.94      0.96    245063
           1       0.45      0.79      0.57     16162

   micro avg       0.93      0.93      0.93    261225
   macro avg       0.72      0.86      0.77    261225
weighted avg       0.95      0.93      0.94    261225



array([[229313,  15750],
       [  3374,  12788]], dtype=int64)